# Analyze missing ttl files in the Spider4SPARQL dataset

In [ ]:
# Missing (empty) database files
missing_ttl = {
    "train": ['bike_1', 'customer_deliveries', 'store_1', 'wine_1', 'chinook_1', 'musical', 'yelp', 'imdb', "academic", "behavior_monitoring", "customer_complaints", "customers_and_addresses", "customers_and_invoices", "customers_and_products_contacts", "customers_campaigns_ecommerce", "customers_card_transactions", "e_government", "flight_1", "geo", "movie_1", "music_2", "pilot_record", "restaurant_1", "restaurants", "roller_coaster", "scholar", "tracking_software_problems", "train_station", "university_basketball", "voter_2"],
    "dev": ["orchestra", "wta_1", "dog_kennels"]
}
# missing_ttl = {
#     "train": ["bike_1", "customer_deliveries"],
#     "dev": []
# }
total_ttls = 166
valid_ttls = total_ttls - len(missing_ttl["train"]) - len(missing_ttl["dev"])
print(f"TTLs valid/total: {valid_ttls}/{total_ttls}")

TTLs valid/total: 133/166


In [ ]:
import sqlite3

# DB name to dump
db_name = "behavior_monitoring"

# Path to the database file
db_path = f"/media/freya/kubuntu-data/datasets/Text2Code/spider/database/{db_name}/{db_name}.sqlite"  # Replace with your .sqlite file path
dump_path = f"./data/Spider/dumps/{db_name}.sql"

# Connect to the SQLite database
connection = sqlite3.connect(db_path)

# Open a file to save the dump
with open(dump_path, "w") as dump_file:
    # Use the `iterdump` method to get a full dump of the database
    for line in connection.iterdump():
        dump_file.write(f"{line}\n")

# Close the connection
connection.close()

# Materialize ttl: Automatic materialization code 
(generated with the help of GPT4o)
- [GPT4o conversation](https://chatgpt.com/share/66f8fdb1-90d4-8007-a10f-c5d1ecb4e400)
- We try to materialize the missing ttl files from the original Spider sqlite files
- (!pip install rdflib)

In [157]:
import sqlite3
import os
import rdflib
from rdflib import URIRef, Literal, Namespace, RDF, XSD
from urllib.parse import quote
from datetime import datetime

def generate_turtle_from_sqlite(sqlite_db_path, ttl_output_path):
    # Create the connection to SQLite database
    conn = sqlite3.connect(sqlite_db_path)
    cursor = conn.cursor()

    # Base Prefix and Namespaces
    base_uri = "http://valuenet/ontop/"
    ns = Namespace(base_uri)
    g = rdflib.Graph()
    g.bind("", ns)

    # Generate namespaces for each table
    def table_namespace(table):
        return Namespace(f"{base_uri}{table}#")

    # Function to generate URIs with URL-encoded values
    def generate_uri(table, identifier):
        encoded_id = quote(str(identifier))
        return URIRef(f"{base_uri}{table}/{table}_id={encoded_id}")

    # Function to validate and format datetime strings to ISO 8601
    def validate_and_format_datetime(value):
        try:
            # Try to parse the value to a datetime object
            dt = datetime.strptime(value, "%Y-%m-%d %H:%M:%S")
            return dt.isoformat()  # Convert to ISO 8601 format
        except ValueError:
            return value  # Return as is if not a valid datetime format

    # Process each table
    tables_query = "SELECT name FROM sqlite_master WHERE type='table';"
    cursor.execute(tables_query)
    tables = [row[0] for row in cursor.fetchall()]

    for table in tables:
        # Define and bind a namespace for the table
        table_ns = table_namespace(table.lower())
        g.bind(table.lower(), table_ns)

        # Get columns and data types
        columns_query = f"PRAGMA table_info({table})"
        cursor.execute(columns_query)
        columns_info = cursor.fetchall()
        columns = [col[1] for col in columns_info]

        # Select all data from the table
        select_query = f"SELECT * FROM {table}"
        cursor.execute(select_query)
        rows = cursor.fetchall()

        for row in rows:
            # Generate subject URI for the current row
            subject_uri = generate_uri(table.lower(), row[0])
            g.add((subject_uri, RDF.type, ns[table.lower()]))

            # Add properties for each column
            for idx, value in enumerate(row):
                column_name = columns[idx]

                if value is None:
                    continue

                # Generate a suitable RDF datatype
                if isinstance(value, int):
                    literal_value = Literal(value, datatype=XSD.integer)
                elif isinstance(value, float):
                    literal_value = Literal(value, datatype=XSD.float)
                elif isinstance(value, str):
                    if "date" in column_name.lower() or "time" in column_name.lower():
                        formatted_value = validate_and_format_datetime(value)
                        if formatted_value != value:  # If formatting was successful
                            literal_value = Literal(formatted_value, datatype=XSD.dateTime)
                        else:
                            literal_value = Literal(value, datatype=XSD.string)
                    else:
                        literal_value = Literal(value, datatype=XSD.string)
                else:
                    literal_value = Literal(value)

                # Determine if the column is a foreign key
                cname_low = column_name.lower()
                if "_id" in cname_low and cname_low != f"{table.lower()}_id":
                    foreign_uri = generate_uri(cname_low.split("_id")[0], value)
                    predicate = table_ns[cname_low.upper()]  # Use uppercase for foreign keys
                    g.add((subject_uri, predicate, foreign_uri))
                else:
                    predicate = table_ns[cname_low]  # Use lowercase for other properties
                    g.add((subject_uri, predicate, literal_value))

    # Write the Turtle output
    g.serialize(destination=ttl_output_path, format="turtle")

    # Close the SQLite connection
    conn.close()

In [158]:
# Materialize missing ttl files:
for split in ['dev', 'train']:
    for db_name in missing_ttl[split]:
    # db_name = "behavior_monitoring"
        sqlite_file = f"/media/freya/kubuntu-data/datasets/Text2Code/spider/database/{db_name}/{db_name}.sqlite"
        ttl_output_file = f"./data/Spider/materialized_ttl/{db_name}.ttl"
        
        generate_turtle_from_sqlite(sqlite_file, ttl_output_file)

# dev.wta_1 (62 entries)
# Changes:
# last_name:
#   Treyes Albarracin
# first_name:   
#   Selin Gulseren
# also, had to add `match_id` to the `matches` Table and make it PK
# dev.dog_kennels ()
#   some entries had extra spaces in phone numbers

## Detect DB files which were still not generated using our materialization code:

In [159]:
from collections import Counter
import json

materialized_triples = {
    "train": ['store_1', 'wine_1', 'chinook_1', 'musical', "roller_coaster", "movie_1", "university_basketball", "pilot_record", "train_station", "restaurant_1", "voter_2", "flight_1", "customer_complaints", "tracking_software_problems", "customers_card_transactions", "customers_and_addresses", "customers_and_products_contacts", "e_government", "customers_campaigns_ecommerce", "customers_and_invoices", "behavior_monitoring"],
    "dev": ["orchestra"]
}

materialized_with_big = {
    "train": materialized_triples["train"] + ["baseball_1", "formula_1", "soccer_1"],
    "dev": materialized_triples["dev"]
}

not_materialized_triples = {
    "train": ['yelp', 'imdb', "academic", "geo", "music_2", "restaurants", "scholar"],
    "dev": []
}

# present in train_others.json: ['yelp', 'imdb', "academic", "geo", "restaurants", "scholar"]
# present in train_spider.json: ["music_2"]

In [160]:
print(f'Newly materialized triple stores: {len(materialized_triples["train"])}, {len([materialized_triples["dev"]])}')
new_valit_ttls = valid_ttls + len(materialized_triples["train"]) + len([materialized_triples["dev"]])
print(f"TTLs valid/total: {new_valit_ttls}/{total_ttls}")

Newly materialized triple stores: 21, 1
TTLs valid/total: 155/166


In [161]:
triple_counts = Counter()
for entry in json.load(open("/home/freya/Documents/Fujilab/Conferences/2024/S2CLite paper/data/Spider4SPARQL/raw/train/train.json")):
    triple_counts[entry["kg_name"]] += 1

non_materialized_triple_counts = sum(v for k, v in triple_counts.items() if k in not_materialized_triples["train"])
print(f"{non_materialized_triple_counts} total samples with non-materialized databases.")
print(f'Out of those, only `music_2` is part of `train_spider.json` with sample count: {triple_counts["music_2"]}.')

100 total samples with non-materialized databases.
Out of those, only `music_2` is part of `train_spider.json` with sample count: 100.


# 3) Get relevant Question-SQL pairs for the relevant database files from Spider
--Now we need to get all the Spider data samples, which are using the newly materialized databases.--
- actually, the S4S dataset already contains all the equivalent queries, so the only problem were the not-materialized ttl files

**Bonus**: Clean up the original Spider data. I.e. remove the `not_materialized_triples`
- relevant only for `music_2` (done)
- TODO: remove any questions which are not shared between the datasets

In [162]:
import json
import pathlib

def replace_quotes(in_path: pathlib.Path, in_str='\"', replace_by="'"):
    processed = []
    source = json.load(in_path.open())
    for entry in source:
        entry["question"] = entry["question"].replace(in_str, replace_by)
        processed.append(entry)
    json.dump(source, in_path.with_suffix(".bak.json").open("w"), indent=4)
    json.dump(processed, in_path.open("w"), indent=4)
    return processed

path_to_jsons = {
    "train": pathlib.Path("/media/freya/kubuntu-data/datasets/Text2Code/spider/train_spider.json"),
    "dev": pathlib.Path("/media/freya/kubuntu-data/datasets/Text2Code/spider/dev.json"),
    "others": pathlib.Path("/media/freya/kubuntu-data/datasets/Text2Code/spider/train_others.json"),
}

for split, pth in path_to_jsons.items():
    replace_quotes(pth)

spider = {
    "train": json.load(open(path_to_jsons["train"])),
    "dev": json.load(open(path_to_jsons["dev"]))
}

In [163]:
relevant_entries = {"train": [], "dev": []}
for ds in ["train", "dev"]:
    for entry in spider[ds]:
        if entry["db_id"] in materialized_triples[ds]:
            relevant_entries[ds].append(entry)


In [164]:
print(len(relevant_entries["train"]), len(relevant_entries["dev"]))

1161 40


In [165]:
# do the same for original S4S files to compare if we are missing any entries
import json
path_to_sparql_jsons = {
    "train": "/home/freya/Documents/Fujilab/Conferences/2024/S2CLite paper/data/Spider4SPARQL/raw/train/train.json",
    "dev": "/home/freya/Documents/Fujilab/Conferences/2024/S2CLite paper/data/Spider4SPARQL/raw/dev/dev.json"
}

spider_sparql = {
    "train": json.load(open(path_to_sparql_jsons["train"])),
    "dev": json.load(open(path_to_sparql_jsons["dev"]))
}

In [166]:
from helpers import init_dict

splits = ["dev", "train"]
not_shared = init_dict(splits, set)
for split in splits:
    unique_q_spider = set()
    unique_q_sparql = set()
    for entry in spider[split]:
        unique_q_spider.add(entry["question"])
        if 'What are the create dates' in entry["question"]:
            print(f"SPIDER: {entry['question']}")
    for entry in spider_sparql[split]:
        unique_q_sparql.add(entry["question"])
        if 'What are the create dates' in entry["question"]:
            print(f"SPARQL: {entry['question']}")
    inter = unique_q_spider.intersection(unique_q_sparql)
    not_shared[split] = unique_q_sparql.symmetric_difference(unique_q_spider)

    # remove the non-shared entries
    

    print(len(unique_q_spider), len(unique_q_sparql), len(inter))
print(not_shared["dev"])
print(len(not_shared["train"]))  # not in Spider4SPARQL: "What is the description of the type of the company who concluded its contracts most recently?"

SPIDER: What are the create dates, states, and phone numbers of the votes that were for the contestant named 'Tabatha Gehling'?
SPARQL: What are the create dates, states, and phone numbers of the votes that were for the contestant named 'Tabatha Gehling'?
1032 1032 1032
6961 6961 6961
set()
0


In [167]:
not_shared["train"]

set()

In [168]:
splits = ["dev", "train"]
relevant_entries_sparql = {s: [] for s in splits}
sparql_unique_dbs = {s: set() for s in splits}
for ds in splits:
    for entry in spider_sparql[ds]:
        kg = entry["kg_name"]
        if kg in materialized_triples[ds]:
            relevant_entries_sparql[ds].append(entry)
        sparql_unique_dbs[ds].add(kg)

In [169]:
print(len(relevant_entries_sparql["train"]), len(relevant_entries_sparql["dev"]))
print(f"SPIDER dbs: {sum(len(d) for d in sparql_unique_dbs.values())}. Also includes the 7 that are from 'spider_others.json'. We will filter those out")

1161 40
SPIDER dbs: 160. Also includes the 7 that are from 'spider_others.json'. We will filter those out


In [170]:
# NOTHING is missing, so we can just use the SPARQL code from Spider4SPARQL!!

# 4) Compare execution results between SQL and SPARQL (and Cypher)
[GPT4o relevant conversation](https://chatgpt.com/share/66f9022c-abe0-8007-89b5-4095c82347ca)
1) get results for SQL commands
2) get results for SPARQL commands
3) get results for Cypher commands (using S2CLite)
4) compare

In [171]:
path_spider = {
    "dev": "/media/freya/kubuntu-data/datasets/Text2Code/spider/dev.json",
    "train": "/media/freya/kubuntu-data/datasets/Text2Code/spider/train_spider.json",
    "others": "/media/freya/kubuntu-data/datasets/Text2Code/spider/train_others.json"
}
path_s4s = {
    "dev": "/home/freya/Documents/Fujilab/Conferences/2024/S2CLite paper/data/Spider4SPARQL/raw/dev/dev.json",
    "train": "/home/freya/Documents/Fujilab/Conferences/2024/S2CLite paper/data/Spider4SPARQL/raw/train/train.json"
}
path_s4c = {
    "dev": "/home/freya/Documents/Fujilab/Conferences/2024/S2CLite paper/data/Spider4SPARQL/dev/res_S2CLite/dev.cypher.json",
    "train": "/home/freya/Documents/Fujilab/Conferences/2024/S2CLite paper/data/Spider4SPARQL/train/res_S2CLite/train.cypher.json"
}
path_out_spider = {
    "dev": "/media/freya/kubuntu-data/git/openai/data/Spider/dev_w_res.json",
    "train": "/media/freya/kubuntu-data/git/openai/data/Spider/train_spider_w_res.json",
    "others": "/media/freya/kubuntu-data/git/openai/data/Spider/train_others_w_res.json",
}

## Remove questions which are not shared among the datasets
This way we reduced the dataset 
- **dev**: 1034 -> 1032
- **train**: 
  - 7000 -> 6999 (spider train)
  - 8659 -> 6999 (s4s train)
  - 6900 -> 6899 (s4c train)

### Manually fixed questions:
**DEV:** (6)
```
 "What are the details for the paragraph that includes the text 'Korea ' ?",
 "What are the details for the paragraph that includes the text 'Korea' ?",

 'What is the name of every singer that does not have any song?',
 'What is the sname of every sing that does not have any song?',

 'Which student has enrolled for the most times in any program? List the id, first name, middle name, last name, the number of enrollments and student id',
 'Which student has enrolled for the most times in any program? List the id, first name, middle name, last name, the number of enrollments and student id.'

 'Find the id of the pet owned by student whose last name is ‘Smith’.',
 'Find the id of the pet owned by student whose last name is ‚ÄòSmith‚Äô.',
 
 'Give me Brazil’s population and life expectancies.',
 'Give me Brazil‚Äôs population and life expectancies.',
 
 'How long is the people’s average life expectancy in Central Africa?',
 'How long is the people‚Äôs average life expectancy in Central Africa?',
```

**TRAIN:** (1)
```
TODO: find
```

### Removed questions :
**DEV:** (2)
```
{*'On average, when were the transcripts printed?',
 *'What is the average transcript date?',
 *'What is the date of the earliest transcript issued ?',
 *'When was the earliest transcript printed?',
}
 ```
 **TRAIN:** (1)
The only removed question from `spider_train.json` is:
```
"What is the description of the type of the company who concluded its contracts most recently?"
```

In [172]:
import json
import sqlite3
from rdflib import Graph
from neo4j import GraphDatabase
from settings import Neo4j_ROOT, KG_ROOT, DB_ROOT
from load_ttl_to_neo4j import load_ttl

def remove_questions(dataset: list[dict], questions_to_remove: set | list):
    dataset_new = []
    for entry in dataset:
        q = entry["question"]
        if q in questions_to_remove:
            continue
        dataset_new.append(entry)
    return dataset_new

def save_json_bak(pth: pathlib.Path):
    suffix = pth.suffix
    assert suffix == ".json"
    with pth.with_suffix(f".bak.{suffix}").open("w") as fp:
        json.dump(json.load(pth.open()), fp, indent=4)


# Load JSON files for SQL, SPARQL, and Cypher datasets
for split in ["dev", "train"]:
    pth_spider = pathlib.Path(path_spider[split])
    pth_s4s = pathlib.Path(path_s4s[split])
    pth_s4c = pathlib.Path(path_s4c[split])
    with pth_spider.open() as sql_file, \
        pth_s4s.open() as sparql_file, \
        pth_s4c.open() as cypher_file:
        sql_data = json.load(sql_file)
        sparql_data = json.load(sparql_file)
        cypher_data = json.load(cypher_file)

    # save_json_bak(pth_spider)
    # save_json_bak(pth_s4s)
    # save_json_bak(pth_s4c)

    print(len(sql_data))
    print(len(sparql_data))
    print(len(cypher_data))

    sql_data = remove_questions(sql_data, not_shared[split])
    sparql_data = remove_questions(sparql_data, not_shared[split])
    cypher_data = remove_questions(cypher_data, not_shared[split])

    with pth_spider.open("w") as sql_file, \
        pth_s4s.open("w") as sparql_file, \
        pth_s4c.open("w") as cypher_file:
        json.dump(sql_data, sql_file, indent=4)
        json.dump(sparql_data, sparql_file, indent=4)
        json.dump(cypher_data, cypher_file, indent=4)

    print(len(sql_data))
    print(len(sparql_data))
    print(len(cypher_data))
# # SPARQL dataset settings
# DATASET_PATH = "/path/to/your/knowledge_graph.ttl"  # Change to the path of your RDF dataset

# # SQLite settings
# SQLITE_DB_PATH = "/path/to/your/sqlite_database.db"  # Change to the path of your SQLite database


1032
1032
1032
1032
1032
1032
6999
6999
6899
6999
6999
6899


In [ ]:
import sqlite3
from settings import DB_ROOT

def execute_sql(query, db_name):
    # Connect to SQLite database and execute the SQL query
    path_to_dataset = DB_ROOT.joinpath(db_name).joinpath(db_name).with_suffix(".sqlite")
    with sqlite3.connect(path_to_dataset) as conn:
        cursor = conn.cursor()
        try:
            cursor.execute(query)
            return cursor.fetchall()
        except sqlite3.Error as e:
            return f"Error executing SQL: {e}"
        
def execute_sparql(query, graph):
    # execute SPARQL query using RDFLib
    result = graph.query(query)
    return list(result)

def execute_cypher(query, driver):
    # Connect to Neo4j database and execute the Cypher quer
    with driver.session() as session:
        result = session.run(query)
        return [record.data() for record in result]

def load_db(db_name):
    path_to_dataset = Neo4j_ROOT.joinpath(KG_ROOT).joinpath(db_name).with_suffix(".ttl")
    graph = Graph()
    graph.parse(path_to_dataset, format="ttl")

    load_ttl(db_name)

    return graph

# from settings import Neo4j_URI, Neo4j_AUTH
#
# def find_equivalent_queries(question, sql_data, sparql_data, cypher_data):
#     # Find equivalent queries from each dataset by matching the 'question' field
#     sql_query = next((item for item in sql_data if item['question'] == question), None)
#     sparql_query = next((item for item in sparql_data if item['question'] == question), None)
#     cypher_query = next((item for item in cypher_data if item['question'] == question), None)
#     return sql_query, sparql_query, cypher_query
# 
# 
# driver = GraphDatabase.driver(Neo4j_URI, auth=Neo4j_AUTH)
# # Iterate over questions in SQL dataset and find equivalent queries
# db_name_prev = None
# graph = None
# for sql_entry in sql_data:
#     db_name = sql_entry['db_id']
#     question = sql_entry['question']
#     sql_query, sparql_query, cypher_query = find_equivalent_queries(question, sql_data, sparql_data, cypher_data)

#     if sql_query and sparql_query and cypher_query:
#         print(f"Question: {question}")

#         if db_name != db_name_prev:
#             graph = load_db(db_name)

#         # Execute SQL query
#         sql_result = execute_sql(sql_query['query'], db_name)
#         print("SQL Result:", sql_result)

#         # Execute SPARQL query
#         sparql_result = execute_sparql(sparql_query['query'], graph)
#         print("SPARQL Result:", sparql_result)

#         # Execute Cypher query
#         cypher_result = execute_cypher(cypher_query['cypher'], driver)
#         print("Cypher Result:", cypher_result)

#         # Compare results
#         if sql_result == sparql_result == cypher_result:
#             print("Results are equivalent.")
#         else:
#             print("Results are not equivalent.")

#     db_name_prev = db_name

In [174]:
# TODO
#  - cypher: none is automatically to be generated by GPT4o
#  - cypher: execution errors to be generated by GPT4o
#  ...

### Collect all execution results from Spider SQL commands
- We create `{split}_w_res.json` files, which additionaly contain "result" field with the response from the appropriate DB for each query.
- Further we make a `dev.qa.json` and `train.qa.json` maps, which are dictionaries `{question: result}`.

In [ ]:
import json

# SQLite settings
def get_spider_execution_results(split):
    with open(path_spider[split]) as sql_file:
        sql_data = json.load(sql_file)
    # Iterate over SQL dataset, execute each query, and collect the results
    for sql_entry in sql_data:
        db_name = sql_entry['db_id']
        query = sql_entry['query']
        result = execute_sql(query, db_name)
        sql_entry['result'] = result  # Add the result to the entry

    # Save the modified SQL data to a new JSON file
    output_file_path = path_out_spider[split]  # Change to the desired output path
    with open(output_file_path, 'w') as output_file:
        json.dump(sql_data, output_file, indent=2)
    print(f"Results saved to {output_file_path}")

for split in ["dev", "train", "others"]:
    get_spider_execution_results(split)

Results saved to /media/freya/kubuntu-data/git/openai/data/Spider/dev_w_res.json
Results saved to /media/freya/kubuntu-data/git/openai/data/Spider/train_spider_w_res.json
Results saved to /media/freya/kubuntu-data/git/openai/data/Spider/train_others_w_res.json


In [176]:
splits = ["dev", "train", "others"]
spider_data = {}
for split in splits:
    spider_data[split] = json.load(open(path_spider[split]))

In [177]:
print([len(d) for d in spider_data.values()])
# [1032, 6999, 1659]

[1032, 6999, 1659]


In [178]:
db_names_spider = {e["db_id"] for e in spider_data["others"]}
print(db_names_spider)
# {'geo', 'yelp', 'academic', 'scholar', 'restaurants', 'imdb'}

{'geo', 'yelp', 'academic', 'scholar', 'restaurants', 'imdb'}


In [179]:
import pathlib
from helpers import dump_dict_with_tuple_keys_to_json, load_dict_with_tuple_keys_from_json

splits = ["dev", "train"]
banned_dbs = ["music_2"]
spider_qa_map = {s: dict() for s in splits} 
spider_unique_queries = {s: set() for s in splits}
spider_unique_dbs = {s: set() for s in splits}
qa_map_dump = {
    "dev": pathlib.Path(path_out_spider["dev"]).with_stem("dev.qa"),
    "train": pathlib.Path(path_out_spider["train"]).with_stem("train.qa")
}

for split in splits:
    with open(path_out_spider[split]) as sql_file:
        sql_data = json.load(sql_file)
    
    for i, entry in enumerate(sql_data):
        db_id = entry["db_id"]
        if db_id in banned_dbs:
            continue
        q = entry["question"]
        s = entry["query"]
        a = entry["result"]
        spider_qa_map[split][(q, db_id)] = a
        spider_unique_queries[split].add(s)
        spider_unique_dbs[split].add(db_id)
    print(f"{split}: {len(spider_qa_map[split])}")

    dump_dict_with_tuple_keys_to_json(spider_qa_map[split], qa_map_dump[split].open("w"), indent=2)

print(sum(len(d) for d in spider_unique_dbs.values()))

dev: 1032
train: 6890
159


In [180]:
d = load_dict_with_tuple_keys_from_json(qa_map_dump["dev"].open())
print(d.keys())

dict_keys([('How many singers do we have?', 'concert_singer'), ('What is the total number of singers?', 'concert_singer'), ('Show name, country, age for all singers ordered by age from the oldest to the youngest.', 'concert_singer'), ('What are the names, countries, and ages for every singer in descending order of age?', 'concert_singer'), ('What is the average, minimum, and maximum age of all singers from France?', 'concert_singer'), ('What is the average, minimum, and maximum age for all French singers?', 'concert_singer'), ('Show the name and the release year of the song by the youngest singer.', 'concert_singer'), ('What are the names and release years for all the songs of the youngest singer?', 'concert_singer'), ('What are all distinct countries where singers above age 20 are from?', 'concert_singer'), ('What are  the different countries with singers above age 20?', 'concert_singer'), ('Show all countries and the number of singers in each country.', 'concert_singer'), ('How many 

In [181]:
def count_total_sparql_stats(mat_kgs: dict[list] = None, splits = ["dev", "train"]):
    if mat_kgs is None:
        mat_kgs = {s:[] for s in splits}
    total_executable_questions = Counter()
    total_executable_queries = {s: set() for s in splits}
    unq_dbs = {s: set() for s in splits}
    for split in splits:
        for entry in spider_sparql[split]:
            key = (entry["question"], entry["kg_name"])
            if entry["kg_name"] in mat_kgs[split]:
                continue
            if key not in spider_qa_map[split]:
                continue
            unq_dbs[split].add(entry["kg_name"])
            total_executable_queries[split].add(entry["query"])
            total_executable_questions[split] += 1

    return total_executable_questions, Counter({s: len(v) for s, v in total_executable_queries.items()}), Counter({s: len(v) for s, v in unq_dbs.items()})

# Count total unique executable SPARQL questions
total_sparql_questions_before_mat, total_sparql_queries_before_mat, unq_dbs_before_mat = count_total_sparql_stats(materialized_triples)
total_sparql_questions_wo_big_dbs, total_sparql_queries_wo_big_dbs, unq_dbs_wo_big_dbs = count_total_sparql_stats(materialized_with_big)
total_sparql_questions, total_sparql_queries, unq_dbs_after_mat = count_total_sparql_stats()

print(unq_dbs_before_mat)
print(unq_dbs_wo_big_dbs)
print(unq_dbs_after_mat)


print(f"Spider: {sum(len(v) for v in spider_qa_map.values())}")
print(f"Spider queries: {sum(len(v) for v in spider_unique_queries.values())}")
print("SPARQL Before materialization:")
print(f"\ttotal questions: {total_sparql_questions_before_mat.total()} ({total_sparql_questions_before_mat})")
print(f"\ttotal queries: {total_sparql_queries_before_mat.total()} ({total_sparql_queries_before_mat})")
print(f"total dbs: {unq_dbs_before_mat.total()} ({unq_dbs_before_mat})")
print("SPARQL before mat and without big dbs:")
print(f"\ttotal questions: {total_sparql_questions_wo_big_dbs.total()} ({total_sparql_questions_wo_big_dbs})")
print(f"\ttotal queries: {total_sparql_queries_wo_big_dbs.total()} ({total_sparql_queries_wo_big_dbs})")
print(f"total dbs: {unq_dbs_wo_big_dbs.total()} ({unq_dbs_wo_big_dbs})")
print("SPARQL After materialization:")
print(f"\ttotal questions: {total_sparql_questions.total()} ({total_sparql_questions})")
print(f"\ttotal queries: {total_sparql_queries.total()} ({total_sparql_queries})")
print(f"total dbs: {unq_dbs_after_mat.total()} ({unq_dbs_after_mat})")

Counter({'train': 112, 'dev': 19})
Counter({'train': 109, 'dev': 19})
Counter({'train': 133, 'dev': 20})
Spider: 7922
Spider queries: 4477
SPARQL Before materialization:
	total questions: 6317 (Counter({'train': 5325, 'dev': 992}))
	total queries: 3978 (Counter({'train': 3457, 'dev': 521}))
total dbs: 131 (Counter({'train': 112, 'dev': 19}))
SPARQL before mat and without big dbs:
	total questions: 6141 (Counter({'train': 5149, 'dev': 992}))
	total queries: 3863 (Counter({'train': 3342, 'dev': 521}))
total dbs: 128 (Counter({'train': 109, 'dev': 19}))
SPARQL After materialization:
	total questions: 7518 (Counter({'train': 6486, 'dev': 1032}))
	total queries: 4728 (Counter({'train': 4187, 'dev': 541}))
total dbs: 153 (Counter({'train': 133, 'dev': 20}))


# !TODO: instead mapping only q, map using (q, kg) 
to account for same questions asked in different kgs (there is about 20 of those)

### Make same maps for S4S and S4C
Using `{split}.cypher.json`, we can extract the execution results for both SPARQL queries (`"result [RDF]"`) and Cypher queries (`"result [Neo4j]"`).
1) extract the qa pairs from `{split}.cypher.json` from `result [RDF]` and `result [Neo4j]` fields.
2) process the fields into same format as the qa pairs from `{split}.qa.json`
3) compare the qa pairs (sql vs sparql), (sql vs cypher)
4) mark the unique question entries, which need to be generated using GPT4o (for both sparql and cypher)  

In [182]:
import json
splits = ["dev", "train"]
s2clite_result_jsons = path_s4c
# s2clite_result_jsons = {
#     "dev": "/home/freya/Documents/Fujilab/Conferences/2024/S2CLite paper/data/Spider4SPARQL/dev/res_S2CLite/dev.cypher.json",
#     "train": "/home/freya/Documents/Fujilab/Conferences/2024/S2CLite paper/data/Spider4SPARQL/train/res_S2CLite/train.cypher.json" # DONE
# }

# Load the sql qa map from the files
spider_qa_map = {s: load_dict_with_tuple_keys_from_json(qa_map_dump[s].open()) for s in splits} 
# print(len(spider_qa_map["dev"]))

# Load the s2clite result files
s2clite_results = {}
for split, pth in s2clite_result_jsons.items():
    s2clite_results[split] = json.load(open(pth))

# Extract the RDF and Neo4j result fields and create the qa pairs
s4s_map = {s: {} for s in s2clite_results.keys()}
s4c_map = {s: {} for s in s2clite_results.keys()}
for split, entries in s2clite_results.items():
    for entry in entries:
        q = entry['question']
        kg = entry['kg_name']
        res_s4s = entry["result [RDF]"]
        res_s4c = entry["result [Neo4j]"] 
        if res_s4s is not None:
            s4s_map[split][(q, kg)] = res_s4s
        if res_s4c is not None:
            s4c_map[split][(q, kg)] = res_s4c

In [183]:
print(f'Entries with non-null results.\nDEV\nS4S: {len(s4s_map["dev"])}\nS4C: {len(s4c_map["dev"])}', )
print(f'Entries with non-null results.\nTRAIN\nS4S: {len(s4s_map["train"])}\nS4C: {len(s4c_map["train"])}', )
# """out
# Entries with non-null results.
# DEV
# S4S: 912
# S4C: 891
# Entries with non-null results.
# TRAIN
# S4S: 5784
# S4C: 5591
# """

Entries with non-null results.
DEV
S4S: 1032
S4C: 891
Entries with non-null results.
TRAIN
S4S: 6557
S4C: 5591


In [184]:
len(spider_qa_map["dev"]), len(spider_qa_map["train"])

(1032, 6890)

In [185]:
spider_qa_map["dev"][('What is the total number of singers?', 'concert_singer')]

[[6]]

In [ ]:
from helpers import normalize_result, dict_map_to_list_map

spider_qa_map_norm =  {split: {q: normalize_result(res) for q, res in mp.items()} for split, mp in spider_qa_map.items()}
s4s_list_map = {split: dict_map_to_list_map(val) for split, val in s4s_map.items()}
s4c_list_map = {split: dict_map_to_list_map(val) for split, val in s4c_map.items()}


In [188]:
len(spider_qa_map_norm["dev"]), len(spider_qa_map_norm["train"])

(1032, 6890)

In [189]:
import json
for split in s4s_list_map.keys():
    json.dump({str(k): v for k,v in s4s_list_map[split].items()}, qa_map_dump[split].with_suffix(".s4s.json").open("w"), indent=2)
    json.dump({str(k): v for k,v in s4c_list_map[split].items()}, qa_map_dump[split].with_suffix(".s4c.json").open("w"), indent=2)

In [190]:
# to load it again, do the following
from ast import literal_eval
for split in ["dev", "train"]:
    d_s4s = json.load(qa_map_dump[split].with_suffix(".s4s.json").open())
    d_s4c = json.load(qa_map_dump[split].with_suffix(".s4c.json").open())
    print({literal_eval(k): normalize_result(v) for k,v in d_s4s.items()})
    assert {literal_eval(k): normalize_result(v) for k,v in d_s4s.items()} == s4s_list_map[split]

{('How many singers do we have?', 'concert_singer'): (('6',),), ('What is the total number of singers?', 'concert_singer'): (('6',),), ('Show name, country, age for all singers ordered by age from the oldest to the youngest.', 'concert_singer'): (('Joe Sharp', 'Netherlands', '52'), ('John Nizinik', 'France', '43'), ('Justin Brown', 'France', '29'), ('Rose White', 'France', '41'), ('Timbaland', 'United States', '32'), ('Tribal King', 'France', '25')), ('What are the names, countries, and ages for every singer in descending order of age?', 'concert_singer'): (('Joe Sharp', 'Netherlands', '52'), ('John Nizinik', 'France', '43'), ('Justin Brown', 'France', '29'), ('Rose White', 'France', '41'), ('Timbaland', 'United States', '32'), ('Tribal King', 'France', '25')), ('What is the average, minimum, and maximum age of all singers from France?', 'concert_singer'): (('34.5', '25', '43'),), ('What is the average, minimum, and maximum age for all French singers?', 'concert_singer'): (('34.5', '25

#### 3. compare the qa pair results
Now we have the qa maps for `spider`, `s4s` and `s4c`, we can **compare** how many entries **have/don't have** equivalent **results**. 

In [191]:
import pandas as pd
df_lens = pd.DataFrame.from_dict({"Spider": (len(spider_qa_map_norm["dev"].values()), len(spider_qa_map_norm["train"].values())),
                                  "S4Sparql": (len(s4s_list_map["dev"].values()), len(s4s_list_map["train"].values())),
                                  "S4Cypher": (len(s4c_list_map["dev"].values()), len(s4c_list_map["train"].values()))}, orient="index", columns=["dev", "train"])
# print(len(spider_qa_map_norm["dev"].values()), len(spider_qa_map_norm["train"].values()))
# print(len(s4s_list_map["dev"].values()), len(s4s_list_map["train"].values()))
# print(len(s4c_list_map["dev"].values()), len(s4c_list_map["train"].values()))
print("Total non-empty QA pairs:")
df_lens["total"] = df_lens.sum(axis=1)
print(df_lens)
# """old.0
# Total non-empty QA pairs:
#            dev  train  total
# Spider    1032   6861   7893
# S4Sparql   980   6449   7429
# S4Cypher   893   5565   6458
# """
# """old.1
# Total non-empty QA pairs:
#            dev  train  total
# Spider    1032   6890   7922
# S4Sparql   912   5784   6696
# S4Cypher   891   5591   6482
# """

Total non-empty QA pairs:
           dev  train  total
Spider    1032   6890   7922
S4Sparql  1032   6557   7589
S4Cypher   891   5591   6482


In [192]:
from collections import Counter
equiv = {
    "s4s": {s: [] for s in s4s_list_map.keys()},
    "s4c": {s: [] for s in s4c_list_map.keys()},
    "s4s-v-s4c": {s: [] for s in s4c_list_map.keys()}, 
}

equiv_queries = {
    "s4s": {s: set() for s in s4s_list_map.keys()},
    "s4c": {s: set() for s in s4c_list_map.keys()},
    "s4s-v-s4c": {s: set() for s in s4c_list_map.keys()}, 
}

not_equiv = {
    "s4s": {s: [] for s in s4s_list_map.keys()},
    "s4c": {s: [] for s in s4c_list_map.keys()},
    "s4s-v-s4c": {s: [] for s in s4c_list_map.keys()}, 
}

not_equiv_queries = {
    "s4s": {s: set() for s in s4s_list_map.keys()},
    "s4c": {s: set() for s in s4c_list_map.keys()},
    "s4s-v-s4c": {s: set() for s in s4c_list_map.keys()}, 
}

spider_qq_map = {}
s4s_qq_map = {}
s4c_qq_map = {}
for split in s4s_list_map.keys():
    spider_qq_map[split] = {(entry["question"], entry["db_id"]): entry["query"] for entry in spider_data[split] if entry["query"] is not None}
    s4s_qq_map[split] = {(entry["question"], entry["kg_name"]): entry["query"] for entry in s2clite_results[split] if entry["query"] is not None}
    s4c_qq_map[split] = {(entry["question"], entry["kg_name"]): entry["cypher"] for entry in s2clite_results[split] if entry["cypher"] is not None}

for split, spider_map_split in spider_qa_map_norm.items():
    for q, res_spider in spider_map_split.items():
        q_s4s = s4s_list_map[split].get(q, None)
        q_s4c = s4c_list_map[split].get(q, None)
        if res_spider == q_s4s:
            equiv["s4s"][split].append(q)
            equiv_queries["s4s"][split].add(s4s_qq_map[split][q])
        else:
            not_equiv["s4s"][split].append(q)

        if res_spider == q_s4c:
            equiv["s4c"][split].append(q)
            equiv_queries["s4c"][split].add(s4c_qq_map[split][q])
        else:
            not_equiv["s4c"][split].append(q)
        if q_s4s == q_s4c:
            equiv["s4s-v-s4c"][split].append(q)
            if s4s_qq_map[split].get(q, None) is not None and s4c_qq_map[split].get(q, None) is None:
                # don't count if original query exists, but s4c query is None
                continue
            equiv_queries["s4s-v-s4c"][split].add((s4s_qq_map[split].get(q, None), s4c_qq_map[split].get(q, None)))
        else:
            not_equiv["s4s-v-s4c"][split].append(q)

In [193]:
df_res_match = pd.DataFrame.from_dict({"total": {s: len(e) for s, e in spider_qa_map_norm.items()},
                                       "S4S": {s: len(e) for s, e in equiv["s4s"].items()},
                                       "S4C": {s: len(e) for s, e in equiv["s4c"].items()},
                                       "S4SvS4C": {s: len(e) for s, e in equiv["s4s-v-s4c"].items()}}, orient="index", columns=["dev", "train"])
df_res_not_match = pd.DataFrame.from_dict({"total": {s: len(e) for s, e in spider_qa_map_norm.items()},
                                       "S4S": {s: len(e) for s, e in not_equiv["s4s"].items()},
                                       "S4C": {s: len(e) for s, e in not_equiv["s4c"].items()}}, orient="index", columns=["dev", "train"])
df_res_query_match = pd.DataFrame.from_dict({"total": {s: len(v) for s, v in spider_unique_queries.items()},
                                             "S4S": {s: len(e) for s, e in equiv_queries["s4s"].items()},
                                             "S4C": {s: len(e) for s, e in equiv_queries["s4c"].items()},
                                             "S4SvS4C": {s: len(e) for s, e in equiv_queries["s4s-v-s4c"].items()}}, orient="index", columns=["dev", "train"])
# print(f'total: {len(spider_qa_map_norm["dev"])}, s4s: {len(equiv["s4s"]["dev"])}({len(not_equiv["s4s"]["dev"])}), s4c: {len(equiv["s4c"]["dev"])}({len(not_equiv["s4c"]["dev"])}), s4s-v-s4c: {len(equiv["s4s-v-s4c"]["dev"])}({len(not_equiv["s4s-v-s4c"]["dev"])})')
print("Questions with matching results:")
df_res_match.sum(axis=1)
# """old
# total      7893
# S4S        5076
# S4C        4659
# S4SvS4C    6478
# dtype: int64
# """
# """old.1
# total      7922
# S4S        4725
# S4C        4623
# S4SvS4C    7270
# dtype: int64
# """

Questions with matching results:


total      7922
S4S        5078
S4C        4628
S4SvS4C    6380
dtype: int64

In [194]:
print("Unique queries with matching results:")
df_res_query_match.sum(axis=1)
# """old
# total      4477
# S4S        3202
# S4C        2903
# S4SvS4C    3881
# dtype: int64
# """
# """old.1
# total      4477
# S4S        2950
# S4C        2871
# S4SvS4C    3881
# dtype: int64
# """

Unique queries with matching results:


total      4477
S4S        3189
S4C        2876
S4SvS4C    3704
dtype: int64

In [195]:
df_match_percent = df_res_match/df_res_match.loc["total"]*100
df_match_percent = df_match_percent.rename({"dev": "dev (%)", "train": "train (%)"}, axis="columns")
print(df_match_percent.mean(axis=1))
# """old
# total      100.000000
# S4S         65.393503
# S4C         60.131837
# S4SvS4C     83.678434
# dtype: float64
# """
# """old.1
# total      100.000000
# S4S         60.858128
# S4C         59.664805
# S4SvS4C     91.890702
# dtype: float64
# """

total      100.000000
S4S         66.550458
S4C         59.701089
S4SvS4C     80.241784
dtype: float64


In [196]:
not_equiv["s4s-v-s4c"]

{'dev': [('List all song names by singers above the average age.',
   'concert_singer'),
  ('What are all the song names by singers who are older than average?',
   'concert_singer'),
  ('Which year has most number of concerts?', 'concert_singer'),
  ('What is the year that had the most concerts?', 'concert_singer'),
  ('Show the stadium names without any concert.', 'concert_singer'),
  ('What are the names of the stadiums without any concerts?',
   'concert_singer'),
  ('Show names for all stadiums except for stadiums having a concert in year 2014.',
   'concert_singer'),
  ('What are the names of all stadiums that did not have a concert in 2014?',
   'concert_singer'),
  ('Find the number of concerts happened in the stadium with the highest capacity .',
   'concert_singer'),
  ('What are the number of concerts that occurred in the stadium with the largest capacity ?',
   'concert_singer'),
  ('Find the major and age of students who do not have a cat pet.', 'pets_1'),
  ('What major i

## Now
Now that we have `dev.qa.json` and `train.qa.json`, we can use them as maps to see if our execution results from S4S and S4C are same as the original SQL query.

In [197]:
s4c_list_map

{'dev': {('How many singers do we have?', 'concert_singer'): (('6',),),
  ('What is the total number of singers?', 'concert_singer'): (('6',),),
  ('Show name, country, age for all singers ordered by age from the oldest to the youngest.',
   'concert_singer'): (('Joe Sharp', 'Netherlands', '52'),
   ('John Nizinik', 'France', '43'),
   ('Justin Brown', 'France', '29'),
   ('Rose White', 'France', '41'),
   ('Timbaland', 'United States', '32'),
   ('Tribal King', 'France', '25')),
  ('What are the names, countries, and ages for every singer in descending order of age?',
   'concert_singer'): (('Joe Sharp', 'Netherlands', '52'),
   ('John Nizinik', 'France', '43'),
   ('Justin Brown', 'France', '29'),
   ('Rose White', 'France', '41'),
   ('Timbaland', 'United States', '32'),
   ('Tribal King', 'France', '25')),
  ('What is the average, minimum, and maximum age of all singers from France?',
   'concert_singer'): (('34.5', '25', '43'),),
  ('What is the average, minimum, and maximum age f

In [198]:
spider_qa_map_norm["dev"][('How many singers do we have?', 'concert_singer')]

(('6',),)

In [199]:
s2clite_results['dev'][0]

{'kg_name': 'concert_singer',
 'question': 'How many singers do we have?',
 'query': 'select (count( *) as ?aggregation_all) where { ?t1 a :singer .        }',
 'ast': '{"vars": ["aggregation_all", "t1"], "iri": {}, "nodes": {"t1": {"label": "ROOT__singer"}}, "props": {}, "rels": [], "rel_types": [], "var_nsprop_map": {}, "aggregates": {"aggregation_all": "COUNT(*)"}, "subg": {}, "MATCH": [], "WHERE": [], "WITH": {"aggregation_all": "COUNT(*) AS aggregation_all"}, "WHERE_WITH": [], "UNWIND": {}, "RETURN": ["aggregation_all"], "ORDER BY": {}, "LIMIT": null, "OFFSET": null}',
 'cypher': 'MATCH (t1:ROOT__singer)\nWITH COUNT(*) AS aggregation_all\nRETURN aggregation_all',
 'result [RDF]': [{'aggregation_all': 6}],
 'result [Neo4j]': [{'aggregation_all': 6}]}

In [200]:
def get_err_type(err: str):
    if err is None:
        return None
    return "(" + err.split("(")[1]

In [201]:
from collections import Counter
err_counters = {"dev": Counter(), "train": Counter()}
for split in s2clite_results.keys():
    for res in s2clite_results[split]:
        if res["question"] in equiv["s4s-v-s4c"][split]:
            continue
        err = res.get("error", None)
        if err is not None:
            err_type = get_err_type(err)
            err_counters[split][err_type] += 1

In [202]:
import pandas as pd
df_err_count = pd.DataFrame.from_dict(err_counters).fillna(0).astype(int)
df_err_count

dev  train
(@Visitor)NotImplementedError      120    763
(@Compare)ValuesMismatch            45    157
(@Neo4j)CypherTypeError              4     40
(@Neo4j)CypherSyntaxError           17    153
(@Compare)NumberofResultsMismatch    4    119
(@RDF)SyntaxError                    0    331
(@Visitor)ValueError                 0      1
(@Assembler)IndexError               0      4
(@Visitor)AssertionError             0      8
(@Neo4j)ClientError                  0      1
(@RDF)ValueError                     0      2

In [203]:
print("Total errors:")
df_err_count.sum(axis=0)
# """old
# dev       126
# train    1154
# dtype: int64
# """

Total errors:


dev       190
train    1579
dtype: int64

In [204]:
splits = ["dev", "train"]
res_not_equiv = init_dict(splits, dict)
res_equiv = init_dict(splits, dict)
res_empty = init_dict(splits, dict)
res_unique_queries = {"equivalent": init_dict(splits, set), "not equivalent": init_dict(splits, set), "empty": init_dict(splits, set)}
for split in s4s_list_map.keys():
    for res in s2clite_results[split]:
        q = (res["question"], res["kg_name"])
        err_type = get_err_type(res.get("error", None))
        res_spider = spider_qa_map_norm[split].get(q, None)
        res_s4s = s4s_list_map[split].get(q, None)
        res_s4c = s4c_list_map[split].get(q, None)
        if not res_spider and not res_s4s and not res_s4c:
            res_empty[split][q] = (res_spider, res_s4s, res_s4c, err_type)
            res_unique_queries["empty"][split].add(spider_qq_map[split].get(q,s4s_qq_map[split].get(q, s4c_qq_map[split].get(q, None))))
        elif q in not_equiv['s4s'][split] or q in not_equiv['s4c'][split]:
            res_not_equiv[split][q] = (res_spider, res_s4s, res_s4c, err_type)
            res_unique_queries["not equivalent"][split].add(spider_qq_map[split].get(q,s4s_qq_map[split].get(q, s4c_qq_map[split].get(q, None))))
        else:
            res_equiv[split][q] = (res_spider, res_s4s, res_s4c, err_type)
            res_unique_queries["equivalent"][split].add(spider_qq_map[split].get(q,s4s_qq_map[split].get(q, s4c_qq_map[split].get(q, None))))

In [205]:
import pandas as pd
def convert_to_df(d: dict):
    df_d = {}
    for split in d.keys():
        df_d[split] = pd.DataFrame.from_dict(d[split], orient='index', columns=["Spider", "S4S", "S4C", "Error"])
    return df_d

df_res_not_equiv = convert_to_df(res_not_equiv)
df_res_equiv = convert_to_df(res_equiv)
df_res_empty = convert_to_df(res_empty)
# for split in res_not_equiv.keys():
#     df_res_not_equiv[split] = pd.DataFrame.from_dict(res_not_equiv[split], orient='index', columns=["Spider", "S4S", "S4C", "Error"])

In [206]:
from helpers import count_values
r = {
    "equivalent": count_values(df_res_equiv),
    "not equivalent": count_values(df_res_not_equiv),
    "empty": count_values(df_res_empty)
}
df_res = pd.DataFrame.from_dict(r)
df_res["total"] = df_res.sum(axis=1)
df_res.loc["total"] = df_res.sum(axis=0)
df_res = df_res.transpose()
print("Unique questions with problem:")
print(df_res)
# """old
# Unique questions with problem:
#                  dev  train  total
# equivalent       608   3888   4496
# not equivalent   402   2817   3219
# empty             22    156    178
# total           1032   6861   7893
# """
# """old.1
# Unique questions with problem:
#                  dev  train  total
# equivalent       606   3856   4462
# not equivalent   404   2860   3264
# empty             22    174    196
# total           1032   6890   7922
# """

Unique questions with problem:
                 dev  train  total
equivalent       606   3861   4467
not equivalent   404   2873   3277
empty             22    156    178
total           1032   6890   7922


In [207]:
from helpers import count_values
df_res_unique_queries = pd.DataFrame.from_dict({k: count_values(v) for k, v in res_unique_queries.items()})
df_res_unique_queries["total"] = df_res_unique_queries.sum(axis=1)
df_res_unique_queries.loc["total"] = df_res_unique_queries.sum(axis=0)
df_res_unique_queries = df_res_unique_queries.transpose()
print(f"Unique queries with problem:")
print(df_res_unique_queries)
# """old_x
# Unique queries with problem:
#                 dev  train  total
# equivalent      306   2196   2502
# not equivalent  244   1632   1876
# empty            12     84     96
# total           562   3912   4474
# """
# """old_0
# Unique queries with problem:
#                 dev  train  total
# equivalent      322   2259   2581
# not equivalent  228   1568   1796
# empty            12     84     96
# total           562   3911   4473
# """

Unique queries with problem:
                dev  train  total
equivalent      321   2233   2554
not equivalent  229   1599   1828
empty            12     84     96
total           562   3916   4478


In [208]:
# !pip install openpyxl
import pathlib
stat_folder = pathlib.Path("./data/stats/")
stat_folder.mkdir(exist_ok=True, parents=True)
df_res_not_equiv["dev"].to_excel(stat_folder.joinpath("res_not_equiv.dev.xlsx"))
df_res_not_equiv["train"].to_excel(stat_folder.joinpath("res_not_equiv.train.xlsx"))
df_res_equiv["dev"].to_excel(stat_folder.joinpath("res_equiv.dev.xlsx"))
df_res_equiv["train"].to_excel(stat_folder.joinpath("res_equiv.train.xlsx"))
df_res_empty["dev"].to_excel(stat_folder.joinpath("res_empty.dev.xlsx"))
df_res_empty["train"].to_excel(stat_folder.joinpath("res_empty.train.xlsx"))

# save counts
from pandas import ExcelWriter
with ExcelWriter(stat_folder.joinpath("res_stats.xlsx"), mode="w") as writer:
    df_res.to_excel(writer, sheet_name="unique questions")
with ExcelWriter(stat_folder.joinpath("res_stats.xlsx"), mode="a") as writer:
    df_res_unique_queries.to_excel(writer, sheet_name="unique queries")

In [209]:
df_res_not_equiv["dev"]
# df.to_latex(open("./res_not_equiv.dev.tex", "w"))

Spider  \
(List all song names by singers above the avera...                     ((Gentleman,), (Sun,), (You,))   
(What are all the song names by singers who are...                     ((Gentleman,), (Sun,), (You,))   
(What is the maximum capacity and the average o...                                    ((52500, 730),)   
(What is the average and maximum capacities for...                     ((10621.666666666666, 52500),)   
(Show the stadium name and capacity with most n...                          ((Somerset Park, 11998),)   
...                                                                                               ...   
(List the name of singers that do not have any ...              ((Abigail Johnson,), (Alice Walton,))   
(What is the name of every singer that does not...              ((Abigail Johnson,), (Alice Walton,))   
(What is the feature type name of feature AirCo...                            ((Amenity, eg Pool.,),)   
(Show the property type descriptions of propert...  ((Apartment, Flat, Condo, etc.,), (Field, Mead...   
(What are the names of properties that are eith...  ((longacre,), (parc coliseum,), (parc east,), ...   

                                                                                                  S4S  \
(List all song names by singers above the avera...                     ((Gentleman,), (Sun,), (You,))   
(What are all the song names by singers who are...                     ((Gentleman,), (Sun,), (You,))   
(What is the maximum capacity and the average o...  ((10104, 2106), (11998, 1477), (2000, 864), (3...   
(What is the average and maximum capacities for...  ((10104, 2106), (11998, 1477), (2000, 864), (3...   
(Show the stadium name and capacity with most n...                       ((Somerset Park, 2, 11998),)   
...                                                                                               ...   
(List the name of singers that do not have any ...              ((Abigail Johnson,), (Alice Walton,))   
(What is the name of every singer that does not...              ((Abigail Johnson,), (Alice Walton,))   
(What is the feature type name of feature AirCo...                            ((Amenity, eg Pool.,),)   
(Show the property type descriptions of propert...                            ((Amenity, eg Pool.,),)   
(What are the names of properties that are eith...  ((longacre,), (parc coliseum,), (parc east,), ...   

                                                                                                  S4C  \
(List all song names by singers above the avera...                                               None   
(What are all the song names by singers who are...                                               None   
(What is the maximum capacity and the average o...  ((10104, 2106), (11998, 1477), (2000, 864), (3...   
(What is the average and maximum capacities for...  ((10104, 2106), (11998, 1477), (2000, 864), (3...   
(Show the stadium name and capacity with most n...                       ((Somerset Park, 2, 11998),)   
...                                                                                               ...   
(List the name of singers that do not have any ...                                               None   
(What is the name of every singer that does not...                                               None   
(What is the feature type name of feature AirCo...                                               None   
(Show the property type descriptions of propert...                                               None   
(What are the names of properties that are eith...                                               None   

                                                                            Error  
(List all song names by singers above the avera...  (@Visitor)NotImplementedError  
(What are all the song names by singers who are...  (@Visitor)NotImplementedError  
(What is the maximum capacity and the average o...          

## From res_not_equiv, generate json entries to fix

In [210]:
"""Generate a json with entries like this:
```json
{
	"question": "...", # natural language question
    "db_id": "...", # relevant database name
	"sql": "...", # semantically equivalent SQL query
	"sparql": "...", # semantically equivalent SPARQL query
	"cypher": "...", # semantically equivalent Cypher query
	"sql_exec_out": "...", # output when the 'sql' query is executed on its respective database
	"sparql_exec_out": "...", # output when the 'sparql' query is executed on an equivalent knowledge graph
	"cypher_exec_out": "...", # output when the 'cypher' query is executed on an equivalent knowledge graph
	"error": "..." # detected error in the entry
}
```
"""

'Generate a json with entries like this:\n```json\n{\n\t"question": "...", # natural language question\n    "db_id": "...", # relevant database name\n\t"sql": "...", # semantically equivalent SQL query\n\t"sparql": "...", # semantically equivalent SPARQL query\n\t"cypher": "...", # semantically equivalent Cypher query\n\t"sql_exec_out": "...", # output when the \'sql\' query is executed on its respective database\n\t"sparql_exec_out": "...", # output when the \'sparql\' query is executed on an equivalent knowledge graph\n\t"cypher_exec_out": "...", # output when the \'cypher\' query is executed on an equivalent knowledge graph\n\t"error": "..." # detected error in the entry\n}\n```\n'

In [211]:
import pathlib
splits = ["dev", "train"]
entries_to_fix = init_dict(splits, list)

ssc_root = pathlib.Path("/home/freya/Documents/Fujilab/Conferences/2024/S2CLite paper/data/Spider4SSC/")
path_to_fix_dump = {
    "dev": ssc_root.joinpath("dev.to_fix.json"),
    "train": ssc_root.joinpath("train.to_fix.json")
}
ssc_root.mkdir(exist_ok=True, parents=True)

for split in df_res_not_equiv.keys():
    for entry in df_res_not_equiv[split].itertuples():
        json_entry = {}
        # print(entry)
        key = entry[0]
        q = key[0]
        db_id = key[1]
        json_entry['question'] = q
        json_entry['db_id'] = db_id
        json_entry['sql'] = spider_qq_map[split].get(key, None)
        json_entry['sparql'] = s4s_qq_map[split].get(key, None)
        json_entry['cypher'] = s4c_qq_map[split].get(key, None)
        json_entry['sql_exec_out'] = entry.Spider
        json_entry['sparql_exec_out'] = entry.S4S
        json_entry['cypher_exec_out'] = entry.S4C
        json_entry['error'] = entry.Error
        entries_to_fix[split].append(json_entry)
    json.dump(entries_to_fix[split], path_to_fix_dump[split].open("w"), indent=4)

In [212]:
ssc_root
print(len(entries_to_fix["dev"]), len(entries_to_fix["train"]))

404 2873


## From res_equiv, generate Spider4SSC

In [213]:
splits = ["dev", "train"]
unified_entries = {"spider": init_dict(splits, list), "sparql": init_dict(splits, list), "cypher": init_dict(splits, list)}
path_s4s_preproc = {
    "dev": "/home/freya/Documents/Fujilab/Conferences/2024/S2CLite paper/data/Spider4SPARQL/dev/dev.json",
    "train": "/home/freya/Documents/Fujilab/Conferences/2024/S2CLite paper/data/Spider4SPARQL/train/train.json"
}

sparql_data_dict = {split: json.load(open(path_s4s_preproc[split])) for split in splits}
cypher_data_dict = {split: json.load(open(path_s4c[split])) for split in splits}

for split in splits:
    for e_s in spider_data[split]:
        key = (e_s["question"], e_s["db_id"])
        if key in res_equiv[split].keys():
            unified_entries["spider"][split].append(e_s)
    for e_s4s in sparql_data_dict[split]:
        key = (e_s4s["question"], e_s4s["kg_name"])
        if key in res_equiv[split].keys():
            unified_entries["sparql"][split].append(e_s4s)
    for e_s4c in cypher_data_dict[split]:
        key = (e_s4c["question"], e_s4c["kg_name"])
        if key in res_equiv[split].keys():
            unified_entries["cypher"][split].append(e_s4c)

In [214]:
print(unified_entries["sparql"]["dev"][0])

{'kg_name': 'concert_singer', 'namespaces': ['concert', 'stadium', 'singer_in_concert', 'singer', 'XMLSchema'], 'question': 'How many singers do we have?', 'query': 'select (count( *) as ?aggregation_all) where { ?t1 a :singer .        }', 'answer': ''}


In [215]:
joint = init_dict(splits, list)
for split in splits:
    for e_s, e_s4s, e_s4c in zip(unified_entries["spider"][split], unified_entries["sparql"][split], unified_entries["cypher"][split]):
        assert e_s["question"] == e_s4s["question"]
        assert e_s4s["question"] == e_s4c["question"]
        unified_entry = {
            "db_id": e_s["db_id"],
            "question": e_s["question"],
            "sql": e_s["query"],
            "sparql": e_s4s["query"],
            "cypher": e_s4c["cypher"].replace("\n", " "),
            "namespaces": e_s4s["namespaces"]
        }
        joint[split].append(unified_entry)

df_joint_counts = pd.DataFrame.from_dict(count_values(joint), orient="index", columns=["entries"])
df_joint_counts.loc["total"] = df_joint_counts.sum()
print(df_joint_counts)
# """old
#        entries
# dev        608
# train     3917
# total     4525
# """
# """old.1
#        entries
# dev        606
# train     3857
# total     4463
# """

       entries
dev        606
train     3862
total     4468


In [139]:
joint["train"][100]

{'db_id': 'book_2',
 'question': 'Show the publishers that have publications with price higher than 10000000 and publications with price lower than 5000000.',
 'sql': 'SELECT Publisher FROM publication WHERE Price  >  10000000 INTERSECT SELECT Publisher FROM publication WHERE Price  <  5000000',
 'sparql': 'SELECT DISTINCT ?T1_publisher WHERE { ?T1 a :publication . ?T1 publication:publisher ?T1_publisher . ?T1 publication:price ?T1_price . FILTER(?T1_price > 10000000) . FILTER (?T1_publisher in (?T2_publisher)) .   ?T2 a :publication . ?T2 publication:publisher ?T2_publisher . ?T2 publication:price ?T2_price .  FILTER(?T2_price < 5000000) .             }',
 'cypher': 'MATCH (T1:ROOT__publication) MATCH (T2:ROOT__publication) WHERE T1.publication__price > 10000000 AND T1.publication__publisher IN [T2.publication__publisher] AND T2.publication__price < 5000000 RETURN DISTINCT T1.publication__publisher AS T1_publisher',
 'namespaces': ['XMLSchema', 'publication', 'book']}

In [142]:
import pathlib
ssc_root = pathlib.Path("/home/freya/Documents/Fujilab/Conferences/2024/S2CLite paper/data/Spider4SSC/")
path_s4ssc = {
    "dev": ssc_root.joinpath("dev.json"),
    "train": ssc_root.joinpath("train.json")
}
ssc_root.mkdir(exist_ok=True, parents=True)
for s, pth in path_s4ssc.items():
    json.dump(joint[s], open(pth, "w"), indent=4)

In [143]:
with open(path_s4ssc["train"]) as f:
    print(len(json.load(f)))

3857


In [56]:
# unified question query map for queistions 
qq_map_for_non_matching = {"dev": {}, "train": {}}
df_qq_map_for_non_matching = {}
splits = ["dev", "train"]
for split in splits:
    for q in res_not_equiv[split].keys():
        qq_map_for_non_matching[split][q] = (spider_qq_map[split].get(q,None), s4s_qq_map[split].get(q,None), s4c_qq_map[split].get(q,None))

    df_qq_map_for_non_matching[split] = pd.DataFrame.from_dict(qq_map_for_non_matching[split], orient='index', columns=["Spider", "S4S", "S4C"])

In [57]:
import pathlib
stat_folder = pathlib.Path("./data/stats/")
stat_folder.mkdir(exist_ok=True, parents=True)
df_qq_map_for_non_matching["dev"].to_excel(stat_folder.joinpath("df_qq_map_for_non_matching.dev.xlsx"))
df_qq_map_for_non_matching["train"].to_excel(stat_folder.joinpath("df_qq_map_for_non_matching.train.xlsx"))
# df_qq_map_for_non_matching["dev"].loc["What is the name of the breed with the most dogs?"]

## Find queries which have more than one question and find why S4S has more of queries than Spider
 

In [58]:
# TODO: for each unique query, find the questions and do intersection. Find the ones that Spider4SPARQL has and Spider does not have? Maybe find the ones that point to the same query multiple times only?
from helpers import init_dict, count_values

splits = ["dev", "train"]
qq_map_one_q_only = {"spider": init_dict(splits, dict), "s4s": init_dict(splits, dict), "s4c": init_dict(splits, dict)}
inter = {"s4s": init_dict(splits, dict), "s4c": init_dict(splits, dict)}
for split in splits:
    for q, quer in spider_qq_map[split].items():
        if quer not in qq_map_one_q_only["spider"][split].values():
            qq_map_one_q_only["spider"][split][q] = quer
    for q, quer in s4s_qq_map[split].items():
        if quer not in qq_map_one_q_only["s4s"][split].values():
            qq_map_one_q_only["s4s"][split][q] = quer
    for q, quer in s4c_qq_map[split].items():
        if quer not in qq_map_one_q_only["s4c"][split].values():
            qq_map_one_q_only["s4c"][split][q] = quer

    inter["s4s"][split] = set(qq_map_one_q_only["s4s"][split].keys()).difference(qq_map_one_q_only["spider"][split].keys())
    inter["s4c"][split] = set(qq_map_one_q_only["s4c"][split].keys()).difference(qq_map_one_q_only["spider"][split].keys())

qq_map_one_q_only_counts = {"spider": count_values(qq_map_one_q_only["spider"]),
                            "s4s": count_values(qq_map_one_q_only["s4s"]),
                            "s4c": count_values(qq_map_one_q_only["s4c"])}
inter_counts = {k: count_values(v) for k, v in inter.items()}

In [59]:
qq_map_one_q_only_counts

{'spider': Counter({'train': 3958, 'dev': 562}),
 's4s': Counter({'train': 4417, 'dev': 541}),
 's4c': Counter({'train': 4128, 'dev': 494})}

In [60]:
inter_counts

{'s4s': Counter({'train': 547, 'dev': 2}),
 's4c': Counter({'train': 483, 'dev': 1})}

=>
- There are `547 + 2` questions which should be part of a matching query pair in Spider4SPARQL
- There are `483 + 1` questions which should be part of a matching query pair in Spider4Cypher

**Example from s4s/raw/train.json**:
```json
    {
        "kg_name": "club_1",
        "question": "How many clubs does the student named 'Eric Tai' belong to?",
        "query": "SELECT DISTINCT (count(DISTINCT ?T1_clubname) as ?aggregation_T1_clubname_102 ) WHERE { ?T1 a :club . ?T13 a :member_of_club . ?T13 :member_of_club\\#ref-clubid ?T1 .  ?T1 :club\\#clubname ?T1_clubname . ?T2 :student\\#fname ?T2_fname . ?T2 :student\\#lname ?T2_lname . ?T2 a :student . ?T13 :member_of_club\\#ref-stuid ?T2 .  ?T1 :club\\#clubname ?T1_clubname . ?T2 :student\\#fname ?T2_fname . ?T2 :student\\#lname ?T2_lname . FILTER(?T2_fname = 'Eric' && ?T2_lname = 'Tai') .        }"
    },
    {
        "kg_name": "club_1",
        "question": "Count the number of clubs for which the student named 'Eric Tai' is a member.",
        "query": "SELECT DISTINCT (count(DISTINCT ?T1_clubname) as ?aggregation_T1_clubname_11 ) WHERE { ?T1 a :club . ?T13 a :member_of_club . ?T13 :member_of_club\\#ref-clubid ?T1 .  ?T1 :club\\#clubname ?T1_clubname . ?T2 :student\\#fname ?T2_fname . ?T2 :student\\#lname ?T2_lname . ?T2 a :student . ?T13 :member_of_club\\#ref-stuid ?T2 .  ?T1 :club\\#clubname ?T1_clubname . ?T2 :student\\#fname ?T2_fname . ?T2 :student\\#lname ?T2_lname . FILTER(?T2_fname = 'Eric' && ?T2_lname = 'Tai') .        }"
    },
```
The above have the same query in original Spider.
```sql
SELECT count(DISTINCT t1.clubname) FROM club AS t1 JOIN member_of_club AS t2 ON t1.clubid  =  t2.clubid JOIN student AS t3 ON t2.stuid  =  t3.stuid WHERE t3.fname  =  \"Eric\" AND t3.lname  =  \"Tai\"
```

In [61]:
inter["s4s"]

{'dev': {'What are the ids and names of each document, as well as the number of paragraphs in each?',
  'What are the languages used by the least number of TV Channels and how many channels use it?'},
 'train': {"Check the invoices record and compute the average quantities ordered with the payment method 'MasterCard'.",
  "Compute the average age of the members in the club 'Tennis Club'.",
  'Compute the average number of hosts for parties.',
  'Compute the average profits companies make.',
  "Compute the average salary of the players in the team called 'Boston Red Stockings'.",
  'Compute the average score of submissions.',
  'Compute the mean price of procedures physician John Wen was trained in.',
  'Compute the total amount of payment processed.',
  'Compute the total amount of settlement across all the settlements.',
  "Compute the total order quantities of the product 'photo'.",
  'Compute the total salary that the player with first name Len and last name Barker received between 

In [62]:
# Which KGs do we lose
splits = ["dev", "train"]

valid_kgs = init_dict(splits, set)
for split in splits:
    valid_qs = set(res_equiv[split].keys())
    for entry in spider_data[split]:
        if entry["question"] in valid_qs:
            valid_kgs[split].add(entry["db_id"])

In [63]:
print(count_values(spider_unique_dbs).total())
print(count_values(valid_kgs).total())
for split, dbs in spider_unique_dbs.items():
    print(f"{split}: {dbs - valid_kgs[split]}") 

159
159
dev: set()
train: set()
